* This code formats the Doñana National Park CSIC metheorological data (http://icts.ebd.csic.es/en/datos-meteorologicos) into European Fluxes Database Cluster format (http://www.europe-fluxdata.eu/)

In [1]:
#import pandas as pd
#import datetime as dt
#import os
#import xlrd
#import altair as alt

# Load metheorological data

In [2]:
import pandas as pd
import datetime as dt
import os
import xlrd

In [3]:
cwd  = os.getcwd()
os.chdir("..")
uwd  = os.getcwd()
os.chdir(cwd)

#Directory with the Data
filepath = cwd + '\\Data\\Rainfall\\'
first_file = "Palacio 2016 - 2017.xls"

#First file of the data set is required to start the batch 
data_meteo = pd.read_excel(filepath + first_file, "Datos Diarios")
length_file = len(data_meteo)

#Loop to batch all existing files // Data available till 
for i in range(2017,2021):
    x = i
    y = i + 1
    file_name = filepath +'Palacio '+str(x)+' - '+ str(y)+'.xls'
    
    df = pd.read_excel(file_name,"Datos Diarios")
    length_file += len(df)
    
    data_meteo = pd.concat([data_meteo, df], axis = 0)
    print('The length of your data set up to '+ str(y) +' is  : ' + str(length_file))

The length of your data set up to 2018 is  : 732
The length of your data set up to 2019 is  : 1098
The length of your data set up to 2020 is  : 1465
The length of your data set up to 2021 is  : 1831


In [4]:
data_meteo

Día    TS    TH  Tmax  Tmin  Prec.   DH  Tmed  Osc.    DL  PAcum.
0   2016-09-01  18.2    18  38.0  16.0    0.0  0.0  27.0  22.0   0.0     0.0
1   2016-09-02  18.5  18.2  38.0  17.0    0.0  0.0  27.5  21.0   0.0     0.0
2   2016-09-03  24.1  22.9  41.0  18.0    0.0  0.0  29.5  23.0   0.0     0.0
3   2016-09-04  19.2  17.9  42.0  19.0    0.0  0.0  30.5  23.0   0.0     0.0
4   2016-09-05  19.3  18.5  46.0  19.0    0.0  0.0  32.5  27.0   0.0     0.0
..         ...   ...   ...   ...   ...    ...  ...   ...   ...   ...     ...
361 2021-08-28  16.2  15.6  30.0  15.0    0.0  0.0  22.5  15.0   0.0   398.0
362 2021-08-29  17.6  17.4  30.0  15.0    0.0  0.0  22.5  15.0   0.0   398.0
363 2021-08-30  16.2  15.2  30.0  16.0    0.0  0.0  23.0  14.0   0.0   398.0
364 2021-08-31  15.2  15.4  30.0  25.0    0.0  0.0  27.5   5.0   0.0   398.0
365        NaT   NaN   NaN   NaN   NaN    NaN  8.0   NaN   NaN  65.0   393.5

[1831 rows x 11 columns]

In [5]:
#Remove files without date

data_meteo = data_meteo.dropna(subset=['Día']).rename(columns={'Día': 'date'})  #1831
data_meteo = data_meteo.set_index('date')
data_meteo = data_meteo.dropna(axis=0, how="all")      
data_meteo 

TS    TH  Tmax  Tmin  Prec.   DH  Tmed  Osc.   DL  PAcum.
date                                                                   
2016-09-01  18.2    18  38.0  16.0    0.0  0.0  27.0  22.0  0.0     0.0
2016-09-02  18.5  18.2  38.0  17.0    0.0  0.0  27.5  21.0  0.0     0.0
2016-09-03  24.1  22.9  41.0  18.0    0.0  0.0  29.5  23.0  0.0     0.0
2016-09-04  19.2  17.9  42.0  19.0    0.0  0.0  30.5  23.0  0.0     0.0
2016-09-05  19.3  18.5  46.0  19.0    0.0  0.0  32.5  27.0  0.0     0.0
...          ...   ...   ...   ...    ...  ...   ...   ...  ...     ...
2021-08-27  20.4  19.2  30.0  20.0    0.0  0.0  25.0  10.0  0.0   398.0
2021-08-28  16.2  15.6  30.0  15.0    0.0  0.0  22.5  15.0  0.0   398.0
2021-08-29  17.6  17.4  30.0  15.0    0.0  0.0  22.5  15.0  0.0   398.0
2021-08-30  16.2  15.2  30.0  16.0    0.0  0.0  23.0  14.0  0.0   398.0
2021-08-31  15.2  15.4  30.0  25.0    0.0  0.0  27.5   5.0  0.0   398.0

[1826 rows x 10 columns]

# Format CSIC files into European Fluxes Database Cluster file

In [6]:


#Create time series with daily frequency



time_series = pd.date_range(start='2016-09-01 00:00:00', end='2021-08-31 00:00:00', freq="D")
#time_series = pd.date_range(start='2016-09-01', end='2021-08-31', freq="D")
#time_series = pd.date_range(start='2020-09-01 00:00:00', end='2021-06-31 00:00:00', freq="D")
#time_series = pd.date_range(start='2020-10-01 00:00:00', end='2021-06-08 00:00:00', freq="D")
time_series = pd.DataFrame(time_series).rename(columns={0: 'date'}).set_index('date')


data_meteo = pd.merge(left= time_series, right = data_meteo,
                        how="left", right_index=True, left_index=True).reset_index()

CSIC_variables     = ['date','TS','TH','Tmax','Tmin','Tmed','Osc.','Prec.']

eu_variables       = ['date','TA_S','TA_H','TA_MAX','TA_MIN','TA_MED','TA_OSC','P_RAIN']


df_meteo = data_meteo[CSIC_variables].set_axis(eu_variables , axis=1)

#Calculate 90 days moving average


df_meteo['P_RAIN_7']  = df_meteo['P_RAIN'].rolling(window=7,  center=True, min_periods=1).mean()
df_meteo['P_RAIN_15'] = df_meteo['P_RAIN'].rolling(window=15, center=True, min_periods=1).mean()
df_meteo['P_RAIN_30'] = df_meteo['P_RAIN'].rolling(window=30, center=True, min_periods=1).mean()
df_meteo['P_RAIN_60'] = df_meteo['P_RAIN'].rolling(window=60, center=True, min_periods=1).mean()
df_meteo['P_RAIN_90'] = df_meteo['P_RAIN'].rolling(window=90, center=True, min_periods=1).mean()


#df_meteo['P_RAIN_7']  = df_meteo['P_RAIN'].rolling(window=7, min_periods=1).mean()
#df_meteo['P_RAIN_15'] = df_meteo['P_RAIN'].rolling(window=15, min_periods=1).mean()
#df_meteo['P_RAIN_30'] = df_meteo['P_RAIN'].rolling(window=30, min_periods=1).mean()
#df_meteo['P_RAIN_60'] = df_meteo['P_RAIN'].rolling(window=60 , min_periods=1).mean()
#df_meteo['P_RAIN_90'] = df_meteo['P_RAIN'].rolling(window=90, min_periods=1).mean()


#Compute shifts of 7, 15, 30, 60, 90 days

df_meteo['P_RAIN_7_7']  = df_meteo['P_RAIN_7'].shift(+7) 
df_meteo['P_RAIN_7_15'] = df_meteo['P_RAIN_7'].shift(+15) 
df_meteo['P_RAIN_7_30'] = df_meteo['P_RAIN_7'].shift(+30) 
df_meteo['P_RAIN_7_60'] = df_meteo['P_RAIN_7'].shift(+60) 
df_meteo['P_RAIN_7_90'] = df_meteo['P_RAIN_7'].shift(+90)
df_meteo['P_RAIN_7_120'] = df_meteo['P_RAIN_7'].shift(+120)
df_meteo['P_RAIN_7_150'] = df_meteo['P_RAIN_7'].shift(+150) 
df_meteo['P_RAIN_7_180'] = df_meteo['P_RAIN_7'].shift(+180) 

#Compute shifts of 7, 15, 30, 60, 90 days

df_meteo['P_RAIN_15_7']  = df_meteo['P_RAIN_15'].shift(+7) 
df_meteo['P_RAIN_15_15'] = df_meteo['P_RAIN_15'].shift(+15) 
df_meteo['P_RAIN_15_30'] = df_meteo['P_RAIN_15'].shift(+30) 
df_meteo['P_RAIN_15_60'] = df_meteo['P_RAIN_15'].shift(+60) 
df_meteo['P_RAIN_15_90'] = df_meteo['P_RAIN_15'].shift(+90) 
df_meteo['P_RAIN_15_120'] = df_meteo['P_RAIN_15'].shift(+120)
df_meteo['P_RAIN_15_150'] = df_meteo['P_RAIN_15'].shift(+150) 
df_meteo['P_RAIN_15_180'] = df_meteo['P_RAIN_15'].shift(+180) 

#Compute shifts of 7, 15, 30, 60, 90 days

df_meteo['P_RAIN_30_7']  = df_meteo['P_RAIN_30'].shift(+7) 
df_meteo['P_RAIN_30_15'] = df_meteo['P_RAIN_30'].shift(+15) 
df_meteo['P_RAIN_30_30'] = df_meteo['P_RAIN_30'].shift(+30) 
df_meteo['P_RAIN_30_60'] = df_meteo['P_RAIN_30'].shift(+60) 
df_meteo['P_RAIN_30_90'] = df_meteo['P_RAIN_30'].shift(+90) 
df_meteo['P_RAIN_30_120'] = df_meteo['P_RAIN_30'].shift(+120)
df_meteo['P_RAIN_30_150'] = df_meteo['P_RAIN_30'].shift(+150) 
df_meteo['P_RAIN_30_180'] = df_meteo['P_RAIN_30'].shift(+180) 

#Compute shifts of 7, 15, 30, 60, 90 days

df_meteo['P_RAIN_60_7']  = df_meteo['P_RAIN_60'].shift(+7) 
df_meteo['P_RAIN_60_15'] = df_meteo['P_RAIN_60'].shift(+15) 
df_meteo['P_RAIN_60_30'] = df_meteo['P_RAIN_60'].shift(+30) 
df_meteo['P_RAIN_60_60'] = df_meteo['P_RAIN_60'].shift(+60) 
df_meteo['P_RAIN_60_90'] = df_meteo['P_RAIN_60'].shift(+90)
df_meteo['P_RAIN_60_120'] = df_meteo['P_RAIN_60'].shift(+120)
df_meteo['P_RAIN_60_150'] = df_meteo['P_RAIN_60'].shift(+150) 
df_meteo['P_RAIN_60_180'] = df_meteo['P_RAIN_60'].shift(+180) 

#Compute shifts of 7, 15, 30, 60, 90 days

df_meteo['P_RAIN_90_7']  = df_meteo['P_RAIN_90'].shift(+7) 
df_meteo['P_RAIN_90_15'] = df_meteo['P_RAIN_90'].shift(+15) 
df_meteo['P_RAIN_90_30'] = df_meteo['P_RAIN_90'].shift(+30) 
df_meteo['P_RAIN_90_60'] = df_meteo['P_RAIN_90'].shift(+60) 
df_meteo['P_RAIN_90_90'] = df_meteo['P_RAIN_90'].shift(+90) 
df_meteo['P_RAIN_90_120'] = df_meteo['P_RAIN_90'].shift(+120)
df_meteo['P_RAIN_90_150'] = df_meteo['P_RAIN_90'].shift(+150) 
df_meteo['P_RAIN_90_180'] = df_meteo['P_RAIN_90'].shift(+180)  

#Fill mising data with linear interpolation


df_meteo = df_meteo.interpolate(method='linear', limit_direction ='forward').set_index ('date')

#Export file

df_meteo.to_csv(filepath + "Metheorological_2016_2021.txt")

In [7]:
df_meteo

TA_S  TA_H  TA_MAX  TA_MIN  TA_MED  TA_OSC  P_RAIN
date                                                          
2016-09-01  18.2    18    38.0    16.0    27.0    22.0     0.0
2016-09-02  18.5  18.2    38.0    17.0    27.5    21.0     0.0
2016-09-03  24.1  22.9    41.0    18.0    29.5    23.0     0.0
2016-09-04  19.2  17.9    42.0    19.0    30.5    23.0     0.0
2016-09-05  19.3  18.5    46.0    19.0    32.5    27.0     0.0
...          ...   ...     ...     ...     ...     ...     ...
2021-08-27  20.4  19.2    30.0    20.0    25.0    10.0     0.0
2021-08-28  16.2  15.6    30.0    15.0    22.5    15.0     0.0
2021-08-29  17.6  17.4    30.0    15.0    22.5    15.0     0.0
2021-08-30  16.2  15.2    30.0    16.0    23.0    14.0     0.0
2021-08-31  15.2  15.4    30.0    25.0    27.5     5.0     0.0

[1826 rows x 7 columns]

In [8]:
# Function to add date variables to DataFrame.

def add_date_info(df):
    
    df = df.reset_index()
    df['Timestamp'] = pd.to_datetime(df['date'], unit='ms') 
    df['Year'] = pd.DatetimeIndex(df['Timestamp']).year
    df['Month'] = pd.DatetimeIndex(df['Timestamp']).month
    df['Day'] = pd.DatetimeIndex(df['Timestamp']).day
    df['DOY'] = pd.DatetimeIndex(df['Timestamp']).dayofyear
    return df

df_meteo = add_date_info(df_meteo)

# Plot time series

In [9]:
import altair as alt

In [10]:
def plot(column,min,max):
    plot =alt.Chart(df_meteo).mark_bar(size=1).encode(
        x='Timestamp:T',
        y= column + ':Q',
        color=alt.Color(
            column + ':Q', scale=alt.Scale(scheme='redblue', domain=(min, max))),
        tooltip=[
            alt.Tooltip('Timestamp:T', title='Date'),
            alt.Tooltip(column + ':Q', title=column)
        ]).properties(width=600, height=300)
    return plot

def plot_df(column,min,max):
    plot =alt.Chart(df_meteo).mark_bar(size=1).encode(
        x='Timestamp:T',
        y= column + ':Q',
        color=alt.Color(
            column + ':Q', scale=alt.Scale(scheme='redblue', domain=(min, max))),
        tooltip=[
            alt.Tooltip('Timestamp:T', title='Date'),
            alt.Tooltip(column + ':Q', title=column)
        ]).properties(width=600, height=300)
    return plot

In [11]:
 def plotMonth(column,min,max): 
    plotMonth = alt.Chart(df_meteo).mark_rect().encode(
        x='Year:O',
        y='Month:O',
        color=alt.Color(
            'mean('+ column +'):Q', scale=alt.Scale(scheme='yellowgreenblue', domain=(min, max))),
        tooltip=[
            alt.Tooltip('Year:O', title='Year'),
            alt.Tooltip('Month:O', title='Month'),
            alt.Tooltip('mean('+ column +'):Q', title='column')
        ]).properties(width=600, height=300)
    return plotMonth

In [12]:
def plotMultiple(column,min,max): 
    highlight = alt.selection(
        type='single', on='mouseover', fields=['Year'], nearest=True)

    base = alt.Chart(df_meteo).encode(
        x=alt.X('DOY:Q', scale=alt.Scale(domain=[0, 353], clamp=True)),
        y=alt.Y(column + ':Q', scale=alt.Scale(domain=[min,max])),
        color=alt.Color('Year:O', scale=alt.Scale(scheme='magma')))

    points = base.mark_circle().encode(
        opacity=alt.value(0),
        tooltip=[
            alt.Tooltip('Year:O', title='Year'),
            alt.Tooltip('DOY:Q', title='DOY'),
            alt.Tooltip(column + ':Q', title='NDVI')
        ]).add_selection(highlight)

    lines = base.mark_line().encode(
        size=alt.condition(~highlight, alt.value(1), alt.value(3)))

    plotMultiple = (points + lines).properties(width=600, height=350).interactive()
    return plotMultiple

In [13]:
def plotRange(column,min,max): 
    base = alt.Chart(df_meteo).encode(
        x=alt.X('DOY:Q', scale=alt.Scale(domain=(0, 365))))

    line = base.mark_line().encode(
        y=alt.Y('mean('+ column +'):Q', scale=alt.Scale(domain=(min,max))))

    band = base.mark_errorband(extent='iqr').encode(
        y= column + ':Q')

    plotRange = (line + band).properties(width=600, height=300).interactive()
    return plotRange

In [14]:
plot_rainfall_90 = plot_df('P_RAIN',0,20)
plot_rainfall_90

alt.Chart(...)

In [15]:
plot_rainfall_90_90 = plot_df('P_RAIN',0,20)
plot_rainfall_90_90

alt.Chart(...)

In [16]:
plot_rainfall_90_90 = plot_df('P_RAIN_90_60',0,5)
plot_rainfall_90_90

alt.Chart(...)

In [17]:
plot_rainfall_90_90 = plot_df('P_RAIN_7',0,5)
plot_rainfall_90_90

alt.Chart(...)

In [18]:
plot_rainfall_Month = plotMonth('P_RAIN',0,4)
plot_rainfall_Month

alt.Chart(...)

In [19]:
df_meteo

data_co_fluxes = df_meteo.copy()


data_co_fluxes = data_co_fluxes.rename(columns={
    'P_RAIN': 'Rainfall (mm/month)',
})


bars = alt.Chart(data_co_fluxes).mark_rect().encode(
    x='Year:O',
    y='Month:O',
    
    color=alt.Color(
        'sum(Rainfall (mm/month)):Q', scale=alt.Scale(scheme='yellowgreenblue', domain=(0, 100))),
    tooltip=[
        alt.Tooltip('Year:O', title='Year'),
        alt.Tooltip('Month:O', title='Month'),
        alt.Tooltip('sum(Rainfall (mm/month)):Q', title='Monthly rainfall [mm/month]')
    ])

text = bars.mark_text(

    color='black',
    dx=7
).encode(
    text='sum(Rainfall (mm/month)):Q',
    color=alt.value('White')   
)


(bars+ text).properties(width=250, height=400).resolve_scale(color='independent').properties(title='Monthly rainfall')


alt.LayerChart(...)

In [20]:
plot_rainfall_Multiple = plotMultiple('P_RAIN',0,40)
plot_rainfall_Multiple

alt.LayerChart(...)

In [21]:
plot_rainfall_Range = plotRange('P_RAIN',0,20)
plot_rainfall_Range

alt.LayerChart(...)

In [22]:
plot_TS = plot('TA_S',0,40)
plot_TS

alt.Chart(...)

In [23]:
plot_TH  = plot('TA_H',0,40)
plot_TH 

alt.Chart(...)

In [24]:
plot_Tmax  = plot('TA_MAX',0,40)
plot_Tmax 

alt.Chart(...)

In [25]:
plot_Tmin  = plot('TA_MIN',0,40)
plot_Tmin 

alt.Chart(...)

In [26]:
plot_Tmed = plot('TA_MED',0,40)
plot_Tmed 

alt.Chart(...)

In [27]:
plot_Tmed_Month = plotMonth('TA_MED',0,30)
plot_Tmed_Month

alt.Chart(...)

In [28]:
plot_Tmed = plot('TA_OSC',0,40)
plot_Tmed 

alt.Chart(...)